# Labrary Import

In [7]:
#from tensorflow.keras.datasets import imdb
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.sequence import pad_sequences

import pandas as pd
import numpy as np
import re 
from soynlp.hangle import compose, decompose, character_is_korean
import os

from collections import Counter
import itertools

# Path Collection

In [35]:
ROOT_PATH = "C:/Users/Seokeeee/Desktop/자연어처리/"
    
DATA_PATH = os.path.join(ROOT_PATH,"Data/")
NSMC_TRAIN_DATA = os.path.join(DATA_PATH,"nsmc_ratings_train.txt")
WATCHA_TEST_DATA = os.path.join(DATA_PATH,"watcha_labeled_test.csv")
YOUTUBE_TEST_DATA = os.path.join(DATA_PATH,"youtube_labeled_test.csv")

RESULT_PATH = os.path.join(ROOT_PATH,"Result/Hypothesis/01/01/")
WORD_MODEL = os.path.join(RESULT_PATH,"Word_Embedding_01_01")

In [13]:
test_01 = pd.read_csv(WATCHA_TEST_DATA, sep=',')
test_02 = pd.read_csv(YOUTUBE_TEST_DATA, sep=',')

In [16]:
data_concat = pd.concat([test_01,test_02])

In [17]:
data_concat

document  label
0                             진짜 너무 재미있게 봤습니다,,????????    1.0
1     이 드라마가 이토록 흥행하는건 모든사람이 하늘성에서 살고싶지만 실은 해체하고싶은 욕...    1.0
2                                     집에 오는 길은 때론 너무 길어    1.0
3     매 화를 보는 내내 힘들었다 선악구도가 부질없어지는 드라마는 처음 긴장감이 마지막화...    1.0
4                         다양한 입맛의 사람들이 모두 만족할만한 맛깔나는 작품    1.0
...                                                 ...    ...
2049  존나게 잘하는 명투수 습관가지고 논하면 재미라도있지왠지 보크같기만 해도 그냥 투수가...    0.0
2050  안경현은 당장 사퇴하고 공식 사과해라 당장해라 나이 처먹고 일베하냐 니네 자식과 가...    0.0
2051  보크규정이라고 있는게 누구에 따라 달라질수 있거나 애매하면 문제가 있는게 아닌가확실...    0.0
2052  안우진도 퇴출시켜야 합니다 학폭은 학폭일뿐 가볍고 무겁고의 차이가 앖습니다 이제부터...    0.0
2053  수비도 역대 유격수 탑이고 참 성실한 선수 같다 휴식일을 줘도 자기가 출전 하겠다고...    1.0

[4054 rows x 2 columns]

In [18]:
### 판다스로 훈련셋과 테스트셋 데이터 로드
train = pd.read_csv(NSMC_TRAIN_DATA, sep='\t')
test = data_concat

print(train.shape)
print(test.shape)

(150000, 3)
(4054, 2)


In [19]:
X_train =  train['document']
X_test = test['document']
Y_train = np.array(train['label'])
Y_test = np.array(test['label'])

In [20]:
doublespace_pattern = re.compile('\s+')

def jamo_sentence(sent): 
  def transform(char): 
    if char == ' ': 
      return char 
    cjj = decompose(char) 
    if len(cjj) == 1: 
      return cjj 
    cjj_ = ''.join(c if c != ' ' else '-' for c in cjj) 
    return cjj_
#sent_ = ''.join(transform(char) for char in sent)
  sent_ =''
  for char in sent: 
    if character_is_korean(char) or char== ' ': 
      sent_ += ''.join(transform(char))
    elif character_is_korean(char) == False:
       sent_ += ''.join(' ')
  sent_ = doublespace_pattern.sub(' ', ''.join(sent_))
  return sent_


In [21]:
X_train =  train['document']
X_train_list=[]
for i in X_train:
  X_train_list.append(jamo_sentence(str(i)))

In [22]:
X_test = test['document']
X_test_list=[]
for i in X_test:
  X_test_list.append(jamo_sentence(str(i)))


# **fasttext 정수** **인코딩** 

In [23]:
corpus = [sent.strip().split(" ") for sent in X_train_list]

In [24]:
words=list(itertools.chain(*corpus))

In [25]:
vocab=Counter(words)
vocab

Counter({'ㅇㅏ-': 2199,
         'ㄷㅓ-ㅂㅣㅇ': 133,
         'ㅈㅣㄴㅉㅏ-': 6712,
         'ㅉㅏ-ㅈㅡㅇㄴㅏ-ㄴㅔ-ㅇㅛ-': 18,
         'ㅁㅗㄱㅅㅗ-ㄹㅣ-': 113,
         'ㅎㅡㅁ': 192,
         'ㅍㅗ-ㅅㅡ-ㅌㅓ-ㅂㅗ-ㄱㅗ-': 20,
         'ㅊㅗ-ㄷㅣㅇㅇㅕㅇㅎㅘ-ㅈㅜㄹ': 1,
         'ㅇㅗ-ㅂㅓ-ㅇㅕㄴㄱㅣ-ㅈㅗ-ㅊㅏ-': 1,
         'ㄱㅏ-ㅂㅕㅂㅈㅣ-': 17,
         'ㅇㅏㄶㄱㅜ-ㄴㅏ-': 3,
         'ㄴㅓ-ㅁㅜ-ㅈㅐ-ㅁㅣㅎㅇㅓㅆㄷㅏ-ㄱㅡ-ㄹㅐ-ㅅㅓ-ㅂㅗ-ㄴㅡㄴㄱㅓㅅㅇㅡㄹㅊㅜ-ㅊㅓㄴㅎㅏㄴㄷㅏ-': 1,
         'ㄱㅛ-ㄷㅗ-ㅅㅗ-': 4,
         'ㅇㅣ-ㅇㅑ-ㄱㅣ-ㄱㅜ-ㅁㅓㄴ': 1,
         'ㅅㅗㄹㅈㅣㄱㅎㅣ-': 998,
         'ㅈㅐ-ㅁㅣ-ㄴㅡㄴ': 309,
         'ㅇㅓㅄㄷㅏ-': 2029,
         'ㅍㅕㅇㅈㅓㅁ': 1985,
         'ㅈㅗ-ㅈㅓㅇ': 11,
         'ㅅㅏ-ㅇㅣ-ㅁㅗㄴㅍㅔ-ㄱㅡ-ㅇㅢ-': 1,
         'ㅇㅣㄱㅅㅏㄹㅅㅡ-ㄹㅓㄴ': 2,
         'ㅇㅕㄴㄱㅣ-ㄱㅏ-': 767,
         'ㄷㅗㄷㅂㅗ-ㅇㅕㅆㄷㅓㄴ': 23,
         'ㅇㅕㅇㅎㅘ-': 19139,
         'ㅅㅡ-ㅍㅏ-ㅇㅣ-ㄷㅓ-ㅁㅐㄴㅇㅔ-ㅅㅓ-': 1,
         'ㄴㅡㄺㅇㅓ-ㅂㅗ-ㅇㅣ-ㄱㅣ-ㅁㅏㄴ': 1,
         'ㅎㅐㅆㄷㅓㄴ': 140,
         'ㅋㅓ-ㅅㅡ-ㅌㅣㄴ': 4,
         'ㄷㅓㄴㅅㅡ-ㅌㅡ-ㄱㅏ-': 1,
         'ㄴㅓ-ㅁㅜ-ㄴㅏ-ㄷㅗ-': 198,
         'ㅇㅣ-ㅃㅓ-ㅂㅗ-ㅇㅕㅆㄷㅏ-': 1,
         'ㅁㅏㄱ': 195,
         'ㄱㅓㄹㅇㅡㅁㅁㅏ-': 1,
         'ㄸㅔㄴ': 2,
         'ㅅㅔ-ㅂㅜ-ㅌㅓ-': 2,
        

In [26]:
len(vocab)

283906

In [27]:
vocab_size=283906
vocab = vocab.most_common(vocab_size) # 등장 빈도수가 높은 상위 5개의 단어만 저장 vocab
vocab

[('ㅇㅕㅇㅎㅘ-', 19139),
 ('ㄴㅓ-ㅁㅜ-', 8575),
 ('ㅈㅓㅇㅁㅏㄹ', 8547),
 ('ㅈㅣㄴㅉㅏ-', 6712),
 ('ㅇㅣ-', 5617),
 ('ㄱㅡ-ㄴㅑㅇ', 3613),
 ('ㅇㅙ-', 3544),
 ('ㅇㅣ-ㄹㅓㄴ', 3498),
 ('ㄷㅓ-', 3313),
 ('ㅈㅓㅁ', 3170),
 ('ㅅㅜ-', 2968),
 ('ㅇㅕㅇㅎㅘ-ㄹㅡㄹ', 2841),
 ('ㄷㅏ-', 2756),
 ('ㅈㅏㄹ', 2695),
 ('ㅈㅗㅁ', 2663),
 ('ㅂㅗ-ㄱㅗ-', 2660),
 ('ㅋ--ㅋ--', 2580),
 ('ㄱㅡ-', 2558),
 ('ㅇㅕㅇㅎㅘ-ㄴㅡㄴ', 2520),
 ('ㅇㅕㅇㅎㅘ-ㄱㅏ-', 2520),
 ('ㅂㅗㄴ', 2317),
 ('ㅂㅘㅆㄴㅡㄴㄷㅔ-', 2291),
 ('ㅊㅚ-ㄱㅗ-ㅇㅢ-', 2265),
 ('ㅇㅏ-', 2199),
 ('ㄴㅐ-ㄱㅏ-', 2142),
 ('ㅇㅣ-ㄱㅓㄴ', 2141),
 ('ㅇㅓㅄㄴㅡㄴ', 2053),
 ('ㄷㅡ-ㄹㅏ-ㅁㅏ-', 2040),
 ('ㅇㅓㅄㄷㅏ-', 2029),
 ('ㅍㅕㅇㅈㅓㅁ', 1985),
 ('ㅇㅘㄴㅈㅓㄴ', 1925),
 ('ㅇㅣ-ㄹㅓㅎㄱㅔ-', 1901),
 ('ㅊㅏㅁ', 1891),
 ('ㅇㅣ-ㄱㅓ-', 1883),
 ('ㄱㅡ-ㄹㅣ-ㄱㅗ-', 1855),
 ('ㅇㅣ-ㄱㅔ-', 1837),
 ('ㅈㅗㅎㅇㅡㄴ', 1794),
 ('ㅇㅣㅆㄴㅡㄴ', 1774),
 ('ㅇㅕㄴㄱㅣ-', 1765),
 ('ㄴㅐ-', 1716),
 ('ㅍㅕㅇㅈㅓㅁㅇㅣ-', 1664),
 ('ㅂㅗ-ㄴㅡㄴ', 1649),
 ('ㄷㅏ-ㅅㅣ-', 1643),
 ('ㅊㅚ-ㄱㅗ-', 1629),
 ('ㅅㅡ-ㅌㅗ-ㄹㅣ-', 1625),
 ('ㅆㅡ-ㄹㅔ-ㄱㅣ-', 1623),
 ('ㅇㅕㄱㅅㅣ-', 1621),
 ('ㄴㅏㄴ', 1529),
 ('ㅋ--', 1511),
 ('ㅁㅏㄶㅇㅣ-', 1505),
 ('ㄱㅓㅅ', 1469),
 ('ㅎㅏㄴ', 1416),
 ('ㅋ--ㅋ--ㅋ--', 1400),
 ('-ㅠ--

In [28]:
word_to_index={} 
i=0 
for (word, frequency) in vocab : 
  i=i+1 
  word_to_index[word]=i 

In [29]:
word_to_index.items()

dict_items([('ㅇㅕㅇㅎㅘ-', 1), ('ㄴㅓ-ㅁㅜ-', 2), ('ㅈㅓㅇㅁㅏㄹ', 3), ('ㅈㅣㄴㅉㅏ-', 4), ('ㅇㅣ-', 5), ('ㄱㅡ-ㄴㅑㅇ', 6), ('ㅇㅙ-', 7), ('ㅇㅣ-ㄹㅓㄴ', 8), ('ㄷㅓ-', 9), ('ㅈㅓㅁ', 10), ('ㅅㅜ-', 11), ('ㅇㅕㅇㅎㅘ-ㄹㅡㄹ', 12), ('ㄷㅏ-', 13), ('ㅈㅏㄹ', 14), ('ㅈㅗㅁ', 15), ('ㅂㅗ-ㄱㅗ-', 16), ('ㅋ--ㅋ--', 17), ('ㄱㅡ-', 18), ('ㅇㅕㅇㅎㅘ-ㄴㅡㄴ', 19), ('ㅇㅕㅇㅎㅘ-ㄱㅏ-', 20), ('ㅂㅗㄴ', 21), ('ㅂㅘㅆㄴㅡㄴㄷㅔ-', 22), ('ㅊㅚ-ㄱㅗ-ㅇㅢ-', 23), ('ㅇㅏ-', 24), ('ㄴㅐ-ㄱㅏ-', 25), ('ㅇㅣ-ㄱㅓㄴ', 26), ('ㅇㅓㅄㄴㅡㄴ', 27), ('ㄷㅡ-ㄹㅏ-ㅁㅏ-', 28), ('ㅇㅓㅄㄷㅏ-', 29), ('ㅍㅕㅇㅈㅓㅁ', 30), ('ㅇㅘㄴㅈㅓㄴ', 31), ('ㅇㅣ-ㄹㅓㅎㄱㅔ-', 32), ('ㅊㅏㅁ', 33), ('ㅇㅣ-ㄱㅓ-', 34), ('ㄱㅡ-ㄹㅣ-ㄱㅗ-', 35), ('ㅇㅣ-ㄱㅔ-', 36), ('ㅈㅗㅎㅇㅡㄴ', 37), ('ㅇㅣㅆㄴㅡㄴ', 38), ('ㅇㅕㄴㄱㅣ-', 39), ('ㄴㅐ-', 40), ('ㅍㅕㅇㅈㅓㅁㅇㅣ-', 41), ('ㅂㅗ-ㄴㅡㄴ', 42), ('ㄷㅏ-ㅅㅣ-', 43), ('ㅊㅚ-ㄱㅗ-', 44), ('ㅅㅡ-ㅌㅗ-ㄹㅣ-', 45), ('ㅆㅡ-ㄹㅔ-ㄱㅣ-', 46), ('ㅇㅕㄱㅅㅣ-', 47), ('ㄴㅏㄴ', 48), ('ㅋ--', 49), ('ㅁㅏㄶㅇㅣ-', 50), ('ㄱㅓㅅ', 51), ('ㅎㅏㄴ', 52), ('ㅋ--ㅋ--ㅋ--', 53), ('-ㅠ--ㅠ-', 54), ('ㅈㅐ-ㅁㅣㅆㄱㅔ-', 55), ('ㅇㅓㅄㄱㅗ-', 56), ('ㄸㅗ-', 57), ('ㅎㅏ-ㄴㅡㄴ', 58), ('ㅇㅏ-ㄲㅏㅂㄷㅏ-', 59), ('', 60), ('ㄲㅗㄱ', 61), ('ㅂㅗ-ㅁㅕㄴ', 62), ('ㅁㅏ-ㅈㅣ-ㅁㅏㄱ', 63), ('ㄱㅏ-ㅈㅏ

In [30]:
X_train_docs =[]
for i in corpus:
  tmp=i
  seq=[]
  for j in tmp:
    if j in word_to_index.keys():
      seq.append(word_to_index[j])
  X_train_docs.append(seq)

In [31]:
import tensorflow as tf
max_len = 100
X_train_docs = tf.keras.preprocessing.sequence.pad_sequences(X_train_docs, maxlen=max_len)

텍스트 데이터 정수 인코딩


In [32]:
corpus = [sent.strip().split(" ") for sent in X_test_list]

In [33]:
X_test_docs =[]
for i in corpus:
  tmp=i
  seq=[]
  for j in tmp:
    if j in word_to_index.keys():
      seq.append(word_to_index[j])
  X_test_docs.append(seq)

In [34]:
X_test_docs = tf.keras.preprocessing.sequence.pad_sequences(X_test_docs, maxlen=max_len)

In [22]:
'''
import tensorflow as tf
max_len = 300
tokenizer = tf.keras.preprocessing.text.Tokenizer(lower=True)
tokenizer.fit_on_texts(X_train_list)
X_train_docs = tokenizer.texts_to_sequences(X_train_list)
X_train_docs = tf.keras.preprocessing.sequence.pad_sequences(X_train_docs, maxlen=max_len)
'''

'\nimport tensorflow as tf\nmax_len = 300\ntokenizer = tf.keras.preprocessing.text.Tokenizer(lower=True)\ntokenizer.fit_on_texts(X_train_list)\nX_train_docs = tokenizer.texts_to_sequences(X_train_list)\nX_train_docs = tf.keras.preprocessing.sequence.pad_sequences(X_train_docs, maxlen=max_len)\n'

In [23]:

#X_test_docs = tokenizer.texts_to_sequences(X_test_list)
#X_test_docs = tf.keras.preprocessing.sequence.pad_sequences(X_test_docs, maxlen=max_len)

In [36]:
from gensim.models import FastText
model = FastText.load(WORD_MODEL) 

In [37]:
vec_dic={}

In [38]:
for i in range(len(model.wv.vectors)):
  vec_dic[model.wv.index2word[i]] = model.wv.vectors[i]

In [39]:
len(vec_dic)
print(len(word_to_index))

283906


In [40]:

MAX_NB_WORDS = 283906 + 1
EMBEDDING_DIM = 300
word_index = words
embedding_matrix = np.zeros((MAX_NB_WORDS, EMBEDDING_DIM))
for word, i in word_to_index.items():
    embedding_vector = vec_dic.get(word)
    
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros
        embedding_matrix[i] = embedding_vector


In [41]:
embedding_matrix

array([[ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.2542195 , -0.19901925,  0.2733849 , ...,  0.33361077,
         0.02941478,  0.09507595],
       [-0.13286477, -0.25448695,  0.46633413, ..., -0.41298535,
         0.07826764, -0.2549547 ],
       ...,
       [-0.08748581,  0.89635271, -0.04538433, ..., -0.48124564,
         0.80288768, -0.50705129],
       [ 1.10131359,  0.2434607 ,  0.56728464, ..., -0.14781186,
         0.83775133, -0.84568042],
       [ 1.16738367, -0.04778155, -0.23805556, ...,  0.11447058,
        -0.12168114, -0.3999694 ]])

In [42]:
class BahdanauAttention(tf.keras.Model):
  def __init__(self, units):
    super(BahdanauAttention, self).__init__()
    self.W1 = Dense(units)
    self.W2 = Dense(units)
    self.V = Dense(1)

  def call(self, values, query): # 단, key와 value는 같음
    # query shape == (batch_size, hidden size)
    # hidden_with_time_axis shape == (batch_size, 1, hidden size)
    # score 계산을 위해 뒤에서 할 덧셈을 위해서 차원을 변경해줍니다.
    hidden_with_time_axis = tf.expand_dims(query, 1)

    # score shape == (batch_size, max_length, 1)
    # we get 1 at the last axis because we are applying score to self.V
    # the shape of the tensor before applying self.V is (batch_size, max_length, units)
    score = self.V(tf.nn.tanh(
        self.W1(values) + self.W2(hidden_with_time_axis)))

    # attention_weights shape == (batch_size, max_length, 1)
    attention_weights = tf.nn.softmax(score, axis=1)

    # context_vector shape after sum == (batch_size, hidden_size)
    context_vector = attention_weights * values
    context_vector = tf.reduce_sum(context_vector, axis=1)

    return context_vector, attention_weights

In [43]:
from tensorflow.keras.layers import Dense, Embedding, Bidirectional, LSTM, Concatenate, Dropout
from tensorflow.keras import Input, Model
from tensorflow.keras import optimizers

In [44]:
vocab_size=283906 + 1
sequence_input = Input(shape=(max_len,), dtype='int32')

embedded_sequences = Embedding(vocab_size, 300, input_length=max_len, weights=[embedding_matrix], mask_zero = True, trainable=False)(sequence_input)

In [45]:
lstm = Bidirectional(LSTM(64, dropout=0.5, return_sequences = True))(embedded_sequences)

In [46]:
lstm, forward_h, forward_c, backward_h, backward_c = Bidirectional \
  (LSTM(64, dropout=0.5, return_sequences=True, return_state=True))(lstm)

In [47]:
print(lstm.shape, forward_h.shape, forward_c.shape, backward_h.shape, backward_c.shape)

(None, 100, 128) (None, 64) (None, 64) (None, 64) (None, 64)


In [48]:
state_h = Concatenate()([forward_h, backward_h]) # 은닉 상태
state_c = Concatenate()([forward_c, backward_c]) # 셀 상태

In [49]:
attention = BahdanauAttention(64) # 가중치 크기 정의
context_vector, attention_weights = attention(lstm, state_h)

In [50]:
dense1 = Dense(20, activation="relu")(context_vector)
dropout = Dropout(0.5)(dense1)
output = Dense(1, activation="sigmoid")(dropout)
model = Model(inputs=sequence_input, outputs=output)

In [51]:
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

In [52]:
history = model.fit(X_train_docs, Y_train, epochs = 10, batch_size = 256, validation_data=(X_test_docs, Y_test), verbose=1)

Epoch 1/10
586/586 [==============================] - 874s 1s/step - loss: 0.4194 - accuracy: 0.8140 - val_loss: nan - val_accuracy: 0.7997
Epoch 2/10
586/586 [==============================] - 919s 2s/step - loss: 0.3741 - accuracy: 0.8368 - val_loss: nan - val_accuracy: 0.8039
Epoch 3/10
586/586 [==============================] - 957s 2s/step - loss: 0.3618 - accuracy: 0.8434 - val_loss: nan - val_accuracy: 0.8007
Epoch 4/10
586/586 [==============================] - 972s 2s/step - loss: 0.3521 - accuracy: 0.8479 - val_loss: nan - val_accuracy: 0.8012
Epoch 5/10
586/586 [==============================] - 969s 2s/step - loss: 0.3474 - accuracy: 0.8508 - val_loss: nan - val_accuracy: 0.7967
Epoch 6/10
586/586 [==============================] - 971s 2s/step - loss: 0.3425 - accuracy: 0.8529 - val_loss: nan - val_accuracy: 0.8051
Epoch 7/10
586/586 [==============================] - 964s 2s/step - loss: 0.3361 - accuracy: 0.8557 - val_loss: nan - val_accuracy: 0.8066
Epoch 8/10
586/586 [

In [53]:
print("\n 테스트 정확도: %.4f" % (model.evaluate(X_test_docs, Y_test)[1]))

127/127 [==============================] - 7s 53ms/step - loss: nan - accuracy: 0.8078

 테스트 정확도: 0.8078


In [54]:
CLASSIFIER_MODEL = os.path.join(RESULT_PATH,"CLASSIFIER_01_01.h5")
CLASSIFIER_MODEL

'C:/Users/Seokeeee/Desktop/자연어처리/Result/Hypothesis/01/01/CLASSIFIER_01_01.h5'

In [55]:
model.save_weights(CLASSIFIER_MODEL)

In [ ]:
'''
model_test = Model(inputs=sequence_input, outputs=output)
model_test.load_weights('/content/gdrive/My Drive/Colab Notebooks/my_lstm/lstm_attention/movie_ft.h5')
'''

In [56]:
X_test_docs # 확인할 필요가 있음.

array([[    0,     0,     0, ...,     2,   114,   183],
       [    0,     0,     0, ...,   123, 44567, 61628],
       [    0,     0,     0, ...,  4849,     2,  9119],
       ...,
       [    0,     0,     0, ...,     2,    50, 11805],
       [    0,     0,     0, ...,  4348, 69146,   446],
       [    0,     0,     0, ...,  2924,   406,    98]])

In [ ]:
#model_test.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
#print("\n 테스트 정확도: %.4f" % (model_test.evaluate(X_test_docs, Y_test)[1]))

In [ ]:
X_test_docs